In [53]:
import pandas as pd
import sqlite3
import json

from geopy.geocoders import Nominatim 
import folium

import io
from PIL import Image, ImageDraw, ImageFont

from compress_curr_popularity_db import extract_features_from_results_blob, compress_popular_times

## Visualize park average popularity overtime
across the day & week

In [3]:
# con = sqlite3.connect('nyc_popularity_20210317_133549.db')
con = sqlite3.connect('pine_grove_cape_may_r2k_popularity_20210316_144723.db')

print('total number of entries: ' + str(list(con.execute("SELECT COUNT(*) FROM popularity"))))


total number of entries: [(4076,)]


In [15]:
philly_popular_times = pd.read_sql_query("SELECT id, raw FROM popularity WHERE has_popular_times > 0", con)
con.close()
philly_popular_times.head()

id  \
0  ChIJAWkAqNL1t4kRlm4slspOSXo   
1  ChIJzcow6Xb1t4kRQVE7s1AWWr8   
2  ChIJ_bk5K1z1t4kRQNverIUOVko   
3  ChIJ_-2cQEX1t4kRoiCrmNMbrQ8   
4  ChIJQWcsgIn2t4kRCL0Ub363FyI   

                                                 raw  
0  ["ChIJAWkAqNL1t4kRlm4slspOSXo", 4.7, 1314, [[7...  
1  ["ChIJzcow6Xb1t4kRQVE7s1AWWr8", 5.0, 4, [[7, [...  
2  ["ChIJ_bk5K1z1t4kRQNverIUOVko", 4.7, 175, [[7,...  
3  ["ChIJAWkAqNL1t4kRlm4slspOSXo", 4.7, 1314, [[7...  
4  ["ChIJQWcsgIn2t4kRCL0Ub363FyI", 4.5, 122, [[7,...

In [24]:
# use the query returned id
philly_popular_times['return_id'] = philly_popular_times['raw'].apply(lambda x: json.loads(x)[0])

philly_popular_times.head()

id  \
0  ChIJAWkAqNL1t4kRlm4slspOSXo   
1  ChIJzcow6Xb1t4kRQVE7s1AWWr8   
2  ChIJ_bk5K1z1t4kRQNverIUOVko   
3  ChIJ_-2cQEX1t4kRoiCrmNMbrQ8   
4  ChIJQWcsgIn2t4kRCL0Ub363FyI   

                                                 raw  \
0  ["ChIJAWkAqNL1t4kRlm4slspOSXo", 4.7, 1314, [[7...   
1  ["ChIJzcow6Xb1t4kRQVE7s1AWWr8", 5.0, 4, [[7, [...   
2  ["ChIJ_bk5K1z1t4kRQNverIUOVko", 4.7, 175, [[7,...   
3  ["ChIJAWkAqNL1t4kRlm4slspOSXo", 4.7, 1314, [[7...   
4  ["ChIJQWcsgIn2t4kRCL0Ub363FyI", 4.5, 122, [[7,...   

                     return_id  
0  ChIJAWkAqNL1t4kRlm4slspOSXo  
1  ChIJzcow6Xb1t4kRQVE7s1AWWr8  
2  ChIJ_bk5K1z1t4kRQNverIUOVko  
3  ChIJAWkAqNL1t4kRlm4slspOSXo  
4  ChIJQWcsgIn2t4kRCL0Ub363FyI

In [28]:
# decompose field,
philly_popular_times[['rating', 'popular_times', 'time_spent']] = philly_popular_times['raw'].apply(extract_features_from_results_blob, args=(
    ['rating', 'popular_times', 'time_spent'], ))

# compress popular_times
philly_popular_times[['popular_times_day', 'popular_times']] = philly_popular_times['popular_times'].apply(compress_popular_times)


In [31]:
philly_popular_times = philly_popular_times.drop(columns=['id', 'raw'])
philly_popular_times.head()

return_id  rating  \
0  ChIJAWkAqNL1t4kRlm4slspOSXo     4.7   
1  ChIJzcow6Xb1t4kRQVE7s1AWWr8     5.0   
2  ChIJ_bk5K1z1t4kRQNverIUOVko     4.7   
3  ChIJAWkAqNL1t4kRlm4slspOSXo     4.7   
4  ChIJQWcsgIn2t4kRCL0Ub363FyI     4.5   

                                       popular_times time_spent  \
0  [[[6, 0], [7, 0], [8, 3], [9, 10], [10, 22], [...   [60, 60]   
1  [[[4, 0], [5, 0], [6, 0], [7, 11], [8, 26], [9...       None   
2  [[[6, 0], [7, 0], [8, 9], [9, 21], [10, 33], [...   [45, 45]   
3  [[[6, 0], [7, 0], [8, 3], [9, 10], [10, 22], [...   [60, 60]   
4  [[[5, 0], [6, 10], [7, 18], [8, 16], [9, 19], ...   [15, 90]   

       popular_times_day  
0  [7, 1, 2, 3, 4, 5, 6]  
1  [7, 1, 2, 3, 4, 5, 6]  
2  [7, 1, 2, 3, 4, 5, 6]  
3  [7, 1, 2, 3, 4, 5, 6]  
4  [7, 1, 2, 3, 4, 5, 6]

In [38]:
# load park info
conn = sqlite3.connect('philly_parks_info.db')
philly_parks = pd.read_sql_query("SELECT id, name, lat, lng FROM info", conn)
conn.close()

philly_parks.head()

id  \
0  ChIJAWkAqNL1t4kRlm4slspOSXo   
1  ChIJzcow6Xb1t4kRQVE7s1AWWr8   
2  ChIJ_bk5K1z1t4kRQNverIUOVko   
3  ChIJ_-2cQEX1t4kRoiCrmNMbrQ8   
4  ChIJQWcsgIn2t4kRCL0Ub363FyI   

                                                name        lat        lng  
0                                  Quiet Waters Park  38.937670 -76.500899  
1                   Hillsmere Shores Community Beach  38.927212 -76.494150  
2                             Quiet Waters Dog Beach  38.930202 -76.508341  
3                              Quiet Waters Dog Park  38.931865 -76.505658  
4  Pip Moyer Recreation Center (Annapolis Recreat...  38.963271 -76.505150

In [39]:
# merge the two table so we have coords
philly_merged = philly_popular_times.merge(philly_parks, left_on='return_id', right_on='id', how='inner')
philly_merged.head()

return_id  rating  \
0  ChIJAWkAqNL1t4kRlm4slspOSXo     4.7   
1  ChIJAWkAqNL1t4kRlm4slspOSXo     4.7   
2  ChIJzcow6Xb1t4kRQVE7s1AWWr8     5.0   
3  ChIJ_bk5K1z1t4kRQNverIUOVko     4.7   
4  ChIJQWcsgIn2t4kRCL0Ub363FyI     4.5   

                                       popular_times time_spent  \
0  [[[6, 0], [7, 0], [8, 3], [9, 10], [10, 22], [...   [60, 60]   
1  [[[6, 0], [7, 0], [8, 3], [9, 10], [10, 22], [...   [60, 60]   
2  [[[4, 0], [5, 0], [6, 0], [7, 11], [8, 26], [9...       None   
3  [[[6, 0], [7, 0], [8, 9], [9, 21], [10, 33], [...   [45, 45]   
4  [[[5, 0], [6, 10], [7, 18], [8, 16], [9, 19], ...   [15, 90]   

       popular_times_day                           id  \
0  [7, 1, 2, 3, 4, 5, 6]  ChIJAWkAqNL1t4kRlm4slspOSXo   
1  [7, 1, 2, 3, 4, 5, 6]  ChIJAWkAqNL1t4kRlm4slspOSXo   
2  [7, 1, 2, 3, 4, 5, 6]  ChIJzcow6Xb1t4kRQVE7s1AWWr8   
3  [7, 1, 2, 3, 4, 5, 6]  ChIJ_bk5K1z1t4kRQNverIUOVko   
4  [7, 1, 2, 3, 4, 5, 6]  ChIJQWcsgIn2t4kRCL0Ub363FyI   

                                                name        lat        lng  
0                                  Quiet Waters Park  38.937670 -76.500899  
1                                  Quiet Waters Park  38.937670 -76.500899  
2                   Hillsmere Shores Community Beach  38.927212 -76.494150  
3                             Quiet Waters Dog Beach  38.930202 -76.508341  
4  Pip Moyer Recreation Center (Annapolis Recreat...  38.963271 -76.505150

In [84]:
# the region for visualization
# 40.04581935518489, -75.35292988785955
# 39.87006413965944, -74.98841982032214
lat_min = 39.87006413965944
lat_max = 40.04581935518489
lng_min = -75.35292988785955
lng_max = -74.98841982032214

philly_center = philly_merged[(lat_min<philly_merged['lat']) & (philly_merged['lat']<lat_max) & 
                              (lng_min<philly_merged['lng']) & (philly_merged['lng']<lng_max)]

In [85]:
philly_center.shape

(287, 9)

In [69]:
philly_center.iloc[0]['popular_times'][-1][10]

[14, 90]

In [ ]:
# visualize their locations
zoom_start = 12
city = "Philadelphia, PA"
geolocator = Nominatim(user_agent="loc_explorer")
    
# center for visualization
address = city
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

order_ind = 0
for day_ind in range(7):
    for hour_ind in range(0,24,2):

        # create map using latitude and longitude values
        map_pa = folium.Map(location=[latitude, longitude], zoom_start=zoom_start)


        # add markers to map
        for index in range(len(philly_center)):
            lat, lng = philly_center.iloc[index][['lat', 'lng']]

            #get popular times
            try:
                popularity = philly_center.iloc[index]['popular_times'][day_ind][hour_ind][1]
            except IndexError:
                popularity = 0

            folium.CircleMarker(
                [lat, lng], radius=popularity/8, color='blue', # radius=5
                fill=True, fill_color='#3186cc', fill_opacity=0.7, 
                parse_html=False).add_to(map_pa)  

        save_pop_dynamics(map_pa, day_ind, hour_ind, order_ind)
        order_ind += 1

/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/sele

/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/sele

/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '
/Users/chengqiu/anaconda3/lib/python3.7/site-packages/sele

In [125]:
day_list = ['Sun', 'Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat']
def save_pop_dynamics(map_obj, day_ind, hour_ind, order_ind):

    img_data = map_obj._to_png()
    img = Image.open(io.BytesIO(img_data))

    # add text
    w, h = img.size
    img_draw = ImageDraw.Draw(img)
    font = ImageFont.truetype('/Library/Fonts/Arial Unicode.ttf', 48)
    img_draw.text((150, 70), '{} {:02d}:00'.format(day_list[day_ind], hour_ind), fill='black', font=font)

    img.save('popularity_dynamics/philly_popularity_dynamic_{:04d}_day{}_hour{}.png'.format(order_ind, day_ind, hour_ind))

In [100]:
img.size

(1366, 768)

In [77]:
map_pa._to_png()

/Users/chengqiu/anaconda3/lib/python3.7/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x05V\x00\x00\x03\x00\x08\x06\x00\x00\x00\xcf><\xc2\x00\x00\x00\tpHYs\x00\x00\x0b\x13\x00\x00\x0b\x13\x01\x00\x9a\x9c\x18\x00\x00 \x00IDATx\x9c\xbc\xbdy\x90$\xe9u\xd8\xf7\xab\xcc\xca\xca\xb3\xee\xbb\xfa\x9c\xe9\xe9\x9d\xd9\x9d\x9d\xdd\xd9\xd9]\x01K\x00\x04\x88\x8b\xa4@\x8a !\x99\x16iR\x14)Z\x87\xc3\n9\x1c\x8a\xa0\xc3\xb6\x82\x0eEX\xb6\xcc\xd0\x1f\x96\x19\xa2C\n\xc9\x87\x0cJ"\t\x1e \t\x80\x00\x01,\x16\x0b\xccbwfg\xe7\xbez\xfa\xaa\xfb\xae\xca\xaa\xca\xaa\xca\xacJ\xff\x91\xdd\xd9S\xdb3\xbb\x03\x06\xa4\x17\xd1\xd1\xddYy|\xf9\x1d\xef{\xef\xf7\xbd\xf7U`\xff\xfe]\xb7\xde\xed\xb1\xb9\xb1\xca\xa1\xec\x97j\xac,ey\xb7X\xd6\x84f\xbbKH\n\x92\xcd$\xb9\xb7\xb5\xc7\x0b\x17^\x04\xe0\xed\xcb\x97\x16\xee\xf1n)\xdd\xab\xd3o\x99\x98\xdd>!)Hz5Kf=\xc1\xce^\x19E\x91\xfd\xe7U*\r\x9c\xf9\x1cE\xd5\x181g\xe8\xce\xe9\xb8}lU\x00\xe0Ee\x85\xd7\xff\xe57x\xf1\'.\x10\xcd\xc7Qd\x85n\xb7\xc3;_z\x87\xd4J\x92\xe6~\x8bO\xfd\x8dO\x00p\xf1\x8b\xdfa\xe9\xf4*\xd1|\x9c^\xaf\xf7\xd8\xb

In [75]:
!pip install selenium

     |████████████████████████████████| 904 kB 8.2 MB/s eta 0:00:01
